In [1]:
import numpy as np
from Bio import Phylo
from io import StringIO
from scipy.special import comb
from utilities import *

np.random.seed(42)

In [71]:
class GenSimulator():
    """
    Base class that provide simulation for one genom
    population_size_over_time - times when change lambda
    """
    def __init__(self, number_of_descendants: int, 
                 population_size_over_time: list,
                 mutation_rate: int,
                 lambda_distributation: list):
        self.number_of_descendants = number_of_descendants
        self.lambda_distributation = lambda_distributation
        self.population_size_over_time = population_size_over_time
        self.mutation_rate = mutation_rate
        
        self.poisson_rate = number_of_descendants*mutation_rate + comb(number_of_descendants,2)/lambda_distributation[0]
        
        self.current_population = {}
        self.tree = None
        self.table = {}
    
    
    def init_population(self):
        for i in range(self.number_of_descendants):
            name = generate_name()
            while name in self.current_population.keys(): name = generate_name()
            self.current_population[name] = "{}:{}".format(name, '{}')
            
    def do_event(self, event_type, *args):
        if event_type == 'coalescence':
            self.do_coalescence(*args)
        elif event_type == 'mutation':
            self.do_mutation(*args)
        else:
            raise 'Type not in list'
    
    def do_coalescence(self, current_linage_number, t, delta_t):
        #print('coalescence')
        name_1 = np.random.choice(list(self.current_population.keys()))
        name_2 = np.random.choice(list(self.current_population.keys()))
        while name_1 == name_2: name_2 = np.random.choice(list(self.current_population.keys()))
        left = self.current_population.pop(name_1)
        right = self.current_population.pop(name_2)
        new_name = '{}_{}'.format(name_1, name_2)
        new_branch = '(' + left + ',' + right + ')' + new_name
        #print('------')
        #print(new_name)
        #print(new_branch)
        self.current_population[new_name] =  new_branch.format(t, t) + ':{}' # можно менять на delta_t
    
    def do_mutation(self, current_linage_number, t, delta_t):
        #print('mutation')
        position = np.random.uniform()
        while position in self.table.keys(): position = np.random.uniform()
        name = np.random.choice(list(self.current_population.keys()))
        self.table[position] = name
        
    def generate(self):
        self.init_population()
        t = 0
        i = 0
        current_limit = self.population_size_over_time[i]
        current_linage_number = self.number_of_descendants
        
        while current_linage_number > 1:
            #print(len(self.current_population))
            generated_t = np.random.poisson(self.poisson_rate)
            if generated_t > current_limit and i < len(self.population_size_over_time) - 1:
                # Nothing happens in this intervals
                i = i + 1
                t = current_limit
                current_limit = self.population_size_over_time[i]
                self.poisson_rate = current_linage_number*self.mutation_rate + comb(current_linage_number,2)/self.lambda_distributation[i+1]
                continue
            else:
                t = t + generated_t
                # Chose what happens - mutation or coalesent
                s = current_linage_number*self.mutation_rate + comb(current_linage_number,2)/self.lambda_distributation[i+1]
                event_type = np.random.choice(
                    ['mutation', 'coalescence'],
                    p=[current_linage_number*self.mutation_rate/s,
                       (comb(current_linage_number,2)/self.lambda_distributation[i+1])/s]
                )
                self.do_event(event_type, current_linage_number, t, generated_t)
                current_linage_number = len(self.current_population)
                self.poisson_rate = current_linage_number*self.mutation_rate + comb(current_linage_number,2)/self.lambda_distributation[i+1]
        for tree in self.current_population.values():
            self.tree = tree.format(1000)
    
    def __call__(self):
        if self.tree is None:
            raise "Firstly need to be generated"
        return self.tree, self.table
    
    def plot_tree(self):
        handle = StringIO(self.tree)  # parse the newick string
        tree = Phylo.read(handle, "newick")
        matplotlib.rc('font', size=60)
        # set the size of the figure
        fig = plt.figure(figsize=(100, 200), dpi=100)
        # alternatively
        # fig.set_size_inches(10, 20)
        axes = fig.add_subplot(1, 1, 1)
        Phylo.draw(tree, axes=axes)
        return

In [72]:
lam_time = [6,12]
lam = [3,1,3]
mr = 0.25

In [73]:
test = GenSimulator(100, lam_time, mr, lam)
test.generate()
tree_str,mutation = test()

In [75]:
test.plot_tree()

In [76]:
mutation

{0.8938085432166306: 'kNeC',
 0.2729171603243713: 'UnEX',
 0.5478115847248026: 'gXXb_PJFS',
 0.46140119082557607: 'FJos',
 0.5020126243997505: 'NaF5',
 0.6830801734741354: '8eNk_GLIY_N0K8_k2km_y4Ym_SDHD_TNu0_opbD_FVkj_vH3q_aK4f_DVfo_OL0s_RGOW_vtpg',
 0.4752929765655083: 'ElYR_s7gq',
 0.9629539535753299: '4V1e',
 0.9879929924466168: 'yIIv_WYeD_s0uq_VmtW_ikky_Lptx_9rYR_u4vP_FCgb_n7hy_4sxo_qKm9_UM2H_z08T_o8pt_NaF5_7TeW_HdrY_keW1_P0Ti_YrSF_ndSY_IRYs_paqD_ufBV_m958_J8t2_UnEX_pLcb_OPwZ_5rpq_AtGP_vz0f_0htP_gnfu_7MVO_7XRn_jB4r_8eNk_GLIY_N0K8_k2km_y4Ym_SDHD_TNu0_opbD_FVkj_vH3q_aK4f_DVfo_OL0s_RGOW_vtpg',
 0.26305151401193727: 'ElYR_s7gq_pniU_DrER_xkZY_rCIZ_eucs_oZhH_mRPT_ZdLd_K0XT_XIwP_NsfR_SRIf_KElI_eORw_Zek5_ONSW_a0Pa_591M_pzLy_jvCi_Rrjg_8One_glHj_dO6S_ly3q_nuoc_n3pX_FJos_chN6_it6u_Y1xV_dt5i_zb6F_Fh3C_kNeC',
 0.3434305880194931: 'yIIv_WYeD_s0uq_VmtW_ikky_Lptx_9rYR_u4vP_FCgb_n7hy_4sxo_qKm9_UM2H_z08T_o8pt_NaF5_7TeW_HdrY_keW1_P0Ti_YrSF_ndSY_IRYs_paqD_ufBV_m958_J8t2_UnEX_pLcb_OPwZ_5rpq_AtGP_vz0f_0